In [43]:
from math import pi
import pandas as pd
import pandas.io.sql as psql
import numpy as np
import cPickle as pickle
import sqlite3 as sql
import blaze as bz
from odo import odo
from scipy.signal import savgol_filter
from bokeh.plotting import figure, output_notebook, show, ColumnDataSource, vplot, output_server, hplot
from bokeh.models import CustomJS, VBox, HBox, Select, MultiSelect
from bokeh.io import output_file, show, vform, curdoc
from bokeh.charts import BoxPlot
output_notebook()

Loading BokehJS ...

In [8]:
columns_metadata = pd.read_csv("genes_matrix_csv/columns_metadata.csv")
row_metadata = pd.read_csv("genes_matrix_csv/rows_metadata.csv")
expression_data = pd.read_csv("genes_matrix_csv/expression_matrix.csv", header=None)

expression_data = expression_data.T
expression_data.columns = list(row_metadata['gene_symbol'])
expression_data = expression_data.ix[1:].reset_index(drop=True)

full_data = pd.concat([columns_metadata, expression_data], axis=1, join_axes=[expression_data.index])
del full_data['column_num'] #remove column_num column
fixed_columns = full_data.columns[0:7]
brainspan_full_melt = pd.melt(full_data,id_vars=list(fixed_columns), var_name='gene', value_name='rpkm')
del brainspan_full_melt['index']

In [38]:
cats = list("abcdef")
yy = np.random.randn(2000)
g = np.random.choice(cats, 2000)
for i, l in enumerate(cats):
    yy[g == l] += i // 2
df = pd.DataFrame(dict(score=yy, group=g))

In [24]:
#genes = list(brainspan_full_melt['gene'].unique())
#genes = ["ARHGAP19", "FMN2", "UBE2F-SCLY", "WDR4", "ZNF714", "ABCA3", "PRRC2B", "ZNF665", "ABR", "ADAM18", "ADAMDEC1", "AGRN", "AHNAK", "AHNAK2", "AIRE", "ALS2CR11", "AMBRA1", "ANKRD26", "AP5Z1", "APOPT1", "ARFGAP2", "ARHGEF18", "ARSD", "ASB17", "ASH2L", "ASMTL", "ASTE1", "ATF6B", "ATXN7L1", "AUTS2", "AXIN1", "BCLAF1", "BMP4", "BTBD11", "BTN2A1", "C11orf65", "C1orf177", "C1orf86", "C20orf26", "C2CD3", "C3orf30", "C5orf60", "C8orf33", "CAD", "CASC10", "CCDC158", "CCDC33", "CCDC85B", "CCNE2", "CCSER1", "CD97", "CDK15", "CEP68", "CGRRF1", "CHRD", "CHRM4", "CNBD1", "COL18A1", "COL6A6", "COX6C", "CPE", "CRELD2", "CRYBA2", "CSMD2", "CUBN", "DDX27", "DECR2", "DHRSX", "DLK1", "DNAH17", "DNMT3L", "DOCK4", "DSC3", "DSG2", "DSPP", "DYRK3", "DYRK4", "EHBP1L1", "EPG5", "EPHA5", "EPO", "EPRS", "ERMN", "ERRFI1", "ETFDH", "EZH2", "FAM208A", "FAM83H", "FBXO42", "FERMT2", "FHOD3", "FOXJ1", "FRAS1", "FREM3", "GAL3ST3", "GANAB", "GART", "GBA", "GCFC2", "GOLT1A", "GOT1L1", "GPR113", "GPR151", "GPRIN1", "GRM5", "GUCY1A3", "HCN4", "HEPHL1", "HIST1H3A", "IL4I1", "KIAA0586", "KIAA0825", "KIF22", "KLHDC2", "KRTAP10-11", "KRTAP10-7", "LAMA3", "LAMC3", "LAX1", "LETM2", "LINGO1", "LRRC26", "LRRC32", "LSG1", "LY75", "MAPK15", "MARCH7", "MBLAC1", "MCCC1", "MCF2L", "MFSD4", "MICAL3", "MMP1", "MRGPRX1", "MRPL28", "MS4A15", "MSLN", "MUC4", "MYBPHL", "MYO1C", "MYO7A", "NAALAD2", "NDUFA11", "NEO1", "NFATC4", "NID1", "NLRC4", "NOTUM", "NPAP1", "NPHP4", "NPHS1", "NUTM1", "OGDH", "OLAH", "OR10G7", "OR11H6", "OR4D9", "OR8D4", "OR9A4", "OR9I1", "OSBPL8", "OXTR", "PARM1", "PAX9", "PCSK5", "PDZD2", "PELP1", "PERM1", "PEX5L", "PIDD1", "PIK3C2B", "PITRM1", "PKHD1", "PKP3", "PLA2G4C", "PLEKHG4B", "POM121L12", "PPP1R15B", "PPP1R35", "PRR25", "PRR27", "PRR35", "PRSS23", "PRSS27", "PSMD14", "RAB11FIP1", "RFXAP", "RGS21", "RHBDF1", "RIMBP2", "RIN3", "ROBO3", "RPN1", "RPRD2", "RPS6KC1", "SCN9A", "SERPINA4", "SEZ6", "SFTPC", "SGPP2", "SHCBP1L", "SLC14A2", "SLC26A1", "SLC26A9", "SLC2A6", "SLC39A5", "SLC4A4", "SLIT3", "SMAD3", "SMG1", "SNX16", "SOX30", "SPATA18", "SPATS2", "SPIRE2", "SPOCK3", "SPTB", "SRD5A1", "SSH3", "SSPO", "SSRP1", "STBD1", "SYNE3", "SYNGR1", "SYT5", "TAGLN", "TAS1R2", "TCF7", "TECTA", "THAP3", "THOC1", "THPO", "TIGD4", "TLN1", "TMEM14E", "TMEM198", "TMEM249", "TMEM8B", "TNXB", "TRAF5", "TRAPPC10", "TTC16", "TTC21B", "TTN", "TUBGCP6", "TWISTNB", "UFSP1", "UGT2B15", "ULK1", "UMODL1", "UNC79", "USP35", "VWA3A", "VWDE", "WDR27", "WDR7", "WDR90", "WHSC1L1", "WRAP73", "XDH", "ZASP", "ZBTB41", "ZC3H7A", "ZDBF2", "ZFYVE9", "ZNF214", "ZNF423", "ZNF438", "ZNF7", "ZNF765", "ZNFX1", "ZSCAN31"]
genes = ['WDR4', 'RPN1', 'EPHA5', 'WDR7', 'ROBO3', 'MARCH7', 'ZNF665', 'CSMD2', 'FYN', 'SUV420H1', 'ETFB', 'KYNU']

In [17]:
brainspan_db = sql.connect('brainspan.db')
brainspan_full_melt.to_sql('brainspan', brainspan_db)

In [22]:
data_ = bz.Data('sqlite:///brainspan.db')

In [40]:
gene = 'MARCH7'
df = data_.brainspan[data_.brainspan.gene == gene][['gene','structure_name','age','rpkm']]
test_age = brainspan_full_melt[brainspan_full_melt['gene'] == gene][['gene','structure_name','age','rpkm']]

In [45]:
df_ = odo(df, pd.DataFrame, index_col=0)

In [78]:
structures = list(df_.structure_name.unique())
# find the quartiles and IQR for each category
groups = df_.groupby('structure_name')
q1 = groups.quantile(q=0.25)
q2 = groups.quantile(q=0.5)
q3 = groups.quantile(q=0.75)
iqr = q3 - q1
upper = q3 + 1.5*iqr
lower = q1 - 1.5*iqr

# find the outliers for each category
def outliers(group):
    structure = group.name
    return group[(group.rpkm > upper.loc[structure][0]) | (group.rpkm < lower.loc[structure][0])]['rpkm']
out = groups.apply(outliers).dropna()

# prepare outlier data for plotting, we need coordinates for every outlier.
outx = []
outy = []
for structure in structures:
    # only add outliers if they exist
    if not out.loc[structure].empty:
        for value in out[structure]:
            outx.append(structure)
            outy.append(value)

p = figure(tools="save", background_fill_color="#EFE8E2", title="", x_range=structures,  plot_height=1000, plot_width=1000)

# if no outliers, shrink lengths of stems to be no longer than the minimums or maximums
qmin = groups.quantile(q=0.00)
qmax = groups.quantile(q=1.00)
upper.rpkm = [min([x,y]) for (x,y) in zip(list(qmax.iloc[:,0]),upper.rpkm) ]
lower.rpkm = [max([x,y]) for (x,y) in zip(list(qmin.iloc[:,0]),lower.rpkm) ]

# stems
p.segment(structures, upper.rpkm, structures, q3.rpkm, line_width=2, line_color="black")
p.segment(structures, lower.rpkm, structures, q1.rpkm, line_width=2, line_color="black")

# boxes
p.rect(structures, (q3.rpkm+q2.rpkm)/2, 0.7, q3.rpkm-q2.rpkm,
    fill_color=bokeh.palettes.GnBu9[1], line_width=2, line_color="black")
p.rect(structures, (q2.rpkm+q1.rpkm)/2, 0.7, q2.rpkm-q1.rpkm,
    fill_color=bokeh.palettes.GnBu9[3], line_width=2, line_color="black")

# whiskers (almost-0 height rects simpler than segments)
p.rect(structures, lower.rpkm, 0.2, 0.01, line_color="black")
p.rect(structures, upper.rpkm, 0.2, 0.01, line_color="black")

# outliers
p.circle(outx, outy, size=6, color=bokeh.palettes.GnBu9[1], fill_alpha=0.6)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = "white"
p.grid.grid_line_width = 2
p.xaxis.major_label_text_font_size="12pt"
p.xaxis.major_label_orientation = pi/4


show(p)

In [104]:
sources = {}
structure_stats = {}
line = {}
for gene in genes:
    df = brainspan_full_melt[brainspan_full_melt['gene'] == gene][['gene','structure_name','age','rpkm']]
    
    factors = list(df['structure'].unique())
    
    struct_stats = pd.pivot_table(df, 
                                  values='rpkm', 
                                  index='structure',
                                  aggfunc=[np.mean,
                                           np.median,
                                           np.max,
                                           np.min,
                                           lambda x: np.percentile(x, 25),
                                           lambda x: np.percentile(x, 75)]
                                 ).reindex(index=factors)
    struct_stats.columns = [u'mean', u'median', u'max', u'min', u'quartile1', u'quartile3']
    
    struct_stats = struct_stats.reset_index()
    
    struct_stats['iqr'] = struct_stats['quartile3'] - struct_stats['quartile1']
    struct_stats['upper'] = struct_stats['quartile3'] + 1.5*struct_stats['iqr']
    struct_stats['lower'] = struct_stats['quartile1'] - 1.5*struct_stats['iqr']
    struct_stats['mid_point'] = (struct_stats['quartile3']+struct_stats['quartile1'])/2
    

    df_line = pd.pivot_table(df, values='rpkm', index='age', aggfunc=np.mean).to_frame().reindex(index=list(df['age'].unique()))
    df_line = df_line.reset_index()
    df_line['rpkm_smooth'] = savgol_filter(df_line['rpkm'], 31, 3)
    
    structure_stats[str(gene)] = struct_stats
    sources[str(gene)] = df
    line[str(gene)] = df_line
    
    with open('app/data/structure_stats.p', 'w') as fp:
        pickle.dump(structure_stats, fp)
    with open('app/data/sources.p', 'w') as fp:
        pickle.dump(sources, fp)
    with open('app/data/line.p', 'w') as fp:
        pickle.dump(line, fp)

In [230]:
def get_dataset(df, str_list):
    new_df = df[df['structure'].isin(list(str_list))]
    return ColumnDataSource(new_df)


def expression_by_age(source_circle, source_line):
    tools="save"
    factors = list(source_circle.to_df()['age'].unique())
    p = figure(title="Gene Expression by Age",
               background_fill_color="#EFE8E2",
               x_range=factors,
               plot_height=450,
               plot_width=650,
               tools=tools)
    p.circle('age','rpkm', fill_alpha=1, color="#F38630", size=4, source=source_circle)
    p.xaxis.major_label_orientation = pi/4
    p.line('age', 'rpkm_smooth', line_color="#3B8686", line_width=3, source=source_line)
    # change just some things about the x-grid
    p.xgrid.grid_line_color = None
    # change just some things about the y-grid
    p.ygrid.grid_line_alpha = 0.5
    p.ygrid.grid_line_dash = [6, 4]
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = "white"
    p.grid.grid_line_width = 2
    p.xaxis.major_label_text_font_size="7pt"
    return p

def expression_by_structure(source):
    tools="save"
    factors = list(source.to_df()['structure'].unique())
    r = figure(title="Gene Expression by Brain Region",
               background_fill="#EFE8E2",
               x_range=factors,
               plot_height=585,
               plot_width=650,
               tools=tools)
    r.rect('structure',
           'median',
            width=0.6,
            height='iqr',
            source=source)
    r.circle(x='structure', y='rpkm', size=0.1, source=source)
    r.segment('structure','lower','structure','upper', line_width=2, source=source)
    r.rect('structure', 'lower', 0.2, 0.01, source=source)
    r.rect('structure', 'upper', 0.2, 0.01, source=source)
    r.rect('structure', 'median', 0.6, 0.0005, line_color="black", source=source)
    r.xaxis.major_label_orientation = pi/4
    r.xgrid.grid_line_color = None
    r.ygrid.grid_line_color = "white"
    r.ygrid.grid_line_dash = [6, 4]
    r.grid.grid_line_width = 2
    r.xaxis.major_label_text_font_size="7pt"
    return r

In [231]:
def update_plot_structures(attrname, old, new):
    gene = select.value
    src = get_dataset(sources[gene], multi_select.value)
    source2.data.update(src.data)

def update_plot(attrname, old, new):
    gene = str(select.value)
    src1 = ColumnDataSource(structure_stats[gene])
    src2 = ColumnDataSource(sources[gene])
    src3 = ColumnDataSource(line[gene])
    source1.data.update(src1.data)
    source2.data.update(src2.data)
    source3.data.update(src3.data)

genes = ['WDR4', 'RPN1', 'EPHA5', 'WDR7', 'ROBO3', 'MARCH7', 'ZNF665', 'CSMD2', 'FYN', 'SUV420H1', 'ETFB', 'KYNU']

with open('app/data/structure_stats.p', 'rb') as fp1:
    structure_stats = pickle.load(fp1)

with open('app/data/sources.p', 'rb') as fp2:
    sources = pickle.load(fp2)

with open('app/data/line.p', 'rb') as fp3:
    line = pickle.load(fp3)

gene = genes[0]

source1 = ColumnDataSource(structure_stats[gene])
source2 = ColumnDataSource(sources[gene])
source3 = ColumnDataSource(line[gene])

structure_plot = expression_by_structure(source1)
age_plot = expression_by_age(source2, source3)

plot = hplot(structure_plot,age_plot)

select = Select(title="Gene:", value=genes[0], options=genes)
select.on_change('value', update_plot)

multi_select = MultiSelect(title="Brain Region:", value=list(sources[gene]['structure'].unique()),
                           options=list(sources[gene]['structure'].unique()))
multi_select.on_change('value', update_plot_structures)

#curdoc().add_root(vplot(select, plot))
show(vplot(select, plot, multi_select))

# Heatmap

In [63]:
from bokeh.models import HoverTool
import bokeh.palettes
from sklearn import preprocessing

def get_heatmap_data(gene_list):
    genes = gene_list
    # process the data
    gene_hm_df = brainspan_full_melt[brainspan_full_melt['gene'].isin(genes)].reset_index()
    del gene_hm_df['index']

    heatmap_source = pd.DataFrame()
    for gene in genes:
        data = gene_hm_df[gene_hm_df['gene'] == gene]
        hm_data = pd.concat([data['gene'], data['structure_name'], data['age'], data['rpkm']], axis=1)

        rpkm = hm_data.rpkm.reshape(-1,1) #returns a numpy array
        min_max_scaler = preprocessing.MinMaxScaler()
        rpkm_scaled = min_max_scaler.fit_transform(rpkm)

        hm_data['rpkm_norm'] = rpkm_scaled
        heatmap_source = pd.concat([heatmap_source, hm_data])

    genes_hm_df = heatmap_source.groupby(['gene', 'age']).mean().reset_index()
    pivot_data_norm = genes_hm_df.pivot(index='gene', columns='age', values='rpkm_norm')
    pivot_data = genes_hm_df.pivot(index='gene', columns='age', values='rpkm')


    # Set up the data for plotting. We will need to have values for every
    # pair of age/gene names. Map the rate to a color and size.
    ages = list(gene_hm_df['age'].unique())
    colors = bokeh.palettes.RdPu9
    col_rev = []
    for i in reversed(colors):
        col_rev.append(i)

    gene = []
    age = []
    color = []
    rpkm_norm = []
    rpkm = []
    size = []
    for a in ages:
        for g in genes:
            gene.append(g)
            age.append(a)
            rpkm_ = pivot_data_norm[a][g]
            size.append(rpkm_*30)
            rpkm.append(pivot_data[a][g])
            rpkm_norm.append(rpkm_)
            color.append(col_rev[min(int(rpkm_*10), 8)])

    source = ColumnDataSource(
        data=dict(gene=gene, age=age, color=color, rpkm=rpkm, rpkm_norm=rpkm_norm, size=size)
    )
    return source

def plot_heatmap(source, genes):
    # Generate the plot
    TOOLS = "hover,save"
    factors = list(source.to_df()['age'].unique())

    p = figure(title="Gene Expression by Age",
               x_range=factors, y_range=genes,
               x_axis_location="above", plot_width=900, plot_height=400,
               toolbar_location="left", tools=TOOLS)

    p.grid.grid_line_color = None
    p.axis.axis_line_color = None
    p.axis.major_tick_line_color = None
    p.axis.major_label_text_font_size = "7pt"
    p.axis.major_label_standoff = 0
    p.xaxis.major_label_orientation = pi/3

    p.circle("age", "gene", 1, 1, source=source,
           color="color", line_color=None, size="size")

    p.select_one(HoverTool).tooltips = [
        ('gene', '@gene'),
        ('age', '@age'),
        ('rpkm', '@rpkm'),
    ]
    return p

In [229]:
genes = ['WDR4', 'RPN1', 'EPHA5', 'WDR7', 'ROBO3', 'MARCH7', 'ZNF665', 'CSMD2', 'FYN', 'SUV420H1', 'ETFB', 'KYNU']
data_source = get_heatmap_data(genes)
heatmap = plot_heatmap(data_source, genes)
show(heatmap)      # show the plot

In [64]:
bokeh.palettes.RdPu9

['#49006a',
 '#7a0177',
 '#ae017e',
 '#dd3497',
 '#f768a1',
 '#fa9fb5',
 '#fcc5c0',
 '#fde0dd',
 '#fff7f3']